In [2]:
# import the needed packages
import skmob
from skmob.tessellation.tilers import tiler
from skmob.utils.plot import plot_gdf

import pandas as pd
import geopandas as gpd

import numpy as np

%matplotlib inline
import matplotlib.pyplot as plt
from scipy.spatial import Voronoi,voronoi_plot_2d
from geovoronoi import voronoi_regions_from_coords, points_to_coords
import random
from shapely.geometry import Polygon, Point
import folium

In [43]:
# Creating the squared tesselation, with tiles of 500m for the city of Florence
tess_squared = tiler.get('squared', base_shape='Florence, Italy', meters=500)
print("tiles = %s" %len(tess_squared))
tess_squared.head()

tiles = 880


tile_ID                                           geometry
0       0  POLYGON ((11.14976 43.77454, 11.14976 43.77778...
1       1  POLYGON ((11.14976 43.77778, 11.14976 43.78103...
2       2  POLYGON ((11.14976 43.78103, 11.14976 43.78427...
3       3  POLYGON ((11.14976 43.78427, 11.14976 43.78751...
4       4  POLYGON ((11.14976 43.78751, 11.14976 43.79075...

In [44]:
# Create an output path for the tessellation
output_fp = "data/squared_tess.shp"
tess_squared.to_file(output_fp)

C:\Users\Pavilion\anaconda3\envs\Geospatial\lib\site-packages\geopandas\io\file.py:299: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


In [45]:
# Plot of the squared Tessellation over Florence
plot_gdf(tess_squared, zoom=12)

In [46]:
# Random numbers for the flow
np.random.seed(0)
rand_flow = np.random.randint(1000)
tile1 = np.random.randint(779)
tile2 = np.random.randint(779)
print(rand_flow)
print(tile1)
print(tile2)

684
559
629


In [47]:
# Using the previous numbers we create a csv file to have our flow dataframe
flow = "flow.csv"
fdf = skmob.FlowDataFrame.from_file(flow, tessellation=tess_squared, tile_id='tile_ID')
fdf.head()

flow origin destination
0   684    559         629

In [49]:
# Random flow for the squared tessellation
fdf.plot_flows(zoom=12)

In [51]:
# Plot combining tessellation and the randomly created flow 
map_f = fdf.plot_tessellation(zoom=12)
fdf.plot_flows(map_f=map_f)

In [21]:
#################################################
# H3 TESSELLATION #
#################################################

In [36]:
tess_h3 = tiler.get('h3_tessellation', base_shape='Florence, Italy', meters=500)
print("tiles = %s" %len(tess_h3))
tess_h3.head()

tiles = 134


geometry            H3_INDEX  \
0  POLYGON ((11.23301 43.75921, 11.23118 43.75450...  613028450172665855   
1  POLYGON ((11.27258 43.76777, 11.27075 43.76305...  613028447786106879   
2  POLYGON ((11.28031 43.83413, 11.27847 43.82943...  613028447561711615   
3  POLYGON ((11.22166 43.76107, 11.21983 43.75636...  613028450170568703   
4  POLYGON ((11.22091 43.82130, 11.21908 43.81659...  613028448306200575   

  tile_ID  
0       0  
1       1  
2       2  
3       3  
4       4

In [37]:
# Create an output path for the data
output_fp = "data/hex_tess.shp"
tess_h3.to_file(output_fp)

C:\Users\Pavilion\anaconda3\envs\Geospatial\lib\site-packages\geopandas\io\file.py:299: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


In [38]:
# Random numbers for the flow
np.random.seed(0)
rand_flow = np.random.randint(1000)
tile1 = np.random.randint(133)
tile2 = np.random.randint(133)
print(rand_flow)
print(tile1)
print(tile2)

684
47
117


In [39]:
# Using the previous numbers we create a csv file to have our flow dataframe
flow = "flowh3.csv"
fdf_h3 = skmob.FlowDataFrame.from_file(flow, tessellation=tess_h3, tile_id='tile_ID')
fdf_h3.head()

flow origin destination
0   684     47         117

In [40]:
# Plot of the hexagonal Tessellation over Florence
plot_gdf(tess_h3, zoom=12)

In [41]:
# Random flow for the squared tessellation
fdf_h3.plot_flows(zoom=12)

In [42]:
# Plot combining tessellation and the randomly created flow 
maph3_f = fdf_h3.plot_tessellation(zoom=12)
fdf_h3.plot_flows(map_f=maph3_f)

In [22]:
#################################################
# VORONOI TESSELLATION #
#################################################

In [52]:
def get_convex_hull(tess):
    polygon = tess.at[0, 'geometry']
    for tile in tess['geometry']:
        polygon = polygon.union(tile)
    return polygon.convex_hull

# Defining the randomization generator
def polygon_random_points(poly, num_points):
    min_x, min_y, max_x, max_y = poly.bounds
    points = []
    while len(points) < num_points:
        random_point = Point([random.uniform(min_x, max_x), random.uniform(min_y, max_y)])
        if (random_point.within(poly)):
            points.append([random_point.x, random_point.y])
    return np.array(points)

def to_GeoDataFrame(region_polys):
    name=[]
    for i in range(1, len(region_polys) + 1):
        name.append('cell ' + str(i))
    gdf = gpd.GeoDataFrame(columns=['name','geometry'], crs={'init': 'epsg:4326'})
    gdf['name'] = name
    for index, row in gdf.iterrows():
        gdf.at[index, 'geometry'] = region_polys[index]
    return gdf

def get_voronoi_tessellation(poly_ch, points):
    vor = Voronoi(points, qhull_options='Qbb Qc Qx')
    #fig = voronoi_plot_2d(vor)
    #plt.show()
    region_polys, region_pts = voronoi_regions_from_coords(points, poly_ch)
    tess_voronoi = to_GeoDataFrame(region_polys)
    return tess_voronoi

In [53]:
poly_ch = get_convex_hull(tess_squared)
# Choosing the number of points desired 
points = polygon_random_points(poly_ch, 100)

In [54]:
# Building the voronoi tessellation from the previous convex hull and the random polygon points
tess_voronoi = get_voronoi_tessellation(poly_ch, points)
print("Cells = %s" %len(tess_voronoi))

# Adding a tile_ID column to the dataframe so we can turn it into a flow dataframe later on
tiles = np.arange(0, 100, 1)
tiles
tess_voronoi = tess_voronoi.assign(tile_ID=tiles)

tess_voronoi.head()

Cells = 100


C:\Users\Pavilion\anaconda3\envs\Geospatial\lib\site-packages\pyproj\crs\crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


name                                           geometry  tile_ID
0  cell 1  POLYGON ((11.32826 43.75978, 11.32754 43.76025...        0
1  cell 2  POLYGON ((11.17335 43.79557, 11.15430 43.80374...        1
2  cell 3  POLYGON ((11.34290 43.78573, 11.32650 43.77971...        2
3  cell 4  POLYGON ((11.31061 43.81709, 11.30326 43.82447...        3
4  cell 5  POLYGON ((11.30070 43.82303, 11.30326 43.82447...        4

In [55]:
# Create an output path for the data
output_fp = "data/vor_tess.shp"
tess_voronoi.to_file(output_fp)

C:\Users\Pavilion\anaconda3\envs\Geospatial\lib\site-packages\geopandas\io\file.py:299: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  pd.Int64Index,


In [56]:
# Random numbers for the flow
np.random.seed(0)
rand_flow = np.random.randint(1000)
tile1 = np.random.randint(99)
tile2 = np.random.randint(99)
print(rand_flow)
print(tile1)
print(tile2)

684
47
64


In [59]:
# Using the previous numbers we create a csv file to have our flow dataframe
flow = "flowvor.csv"
fdf_vor = skmob.FlowDataFrame.from_file(flow, tessellation=tess_voronoi, tile_id='tile_ID')
fdf_vor.head()

flow origin destination
0   684     47          64

In [60]:
# Plot of the voronoi Tessellation over Florence
plot_gdf(tess_voronoi, zoom=12)

In [32]:
# Random flow for the squared tessellation
fdf_vor.plot_flows(zoom=12)

In [33]:
# Plot combining tessellation and the randomly created flow 
mapvor_f = fdf_vor.plot_tessellation(zoom=12)
fdf_vor.plot_flows(map_f=mapvor_f)